## Car Predict  ##
* second hand vehicle prices according to features 

In [11]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score, mean_squared_error
from sklearn.compose import ColumnTransformer # Sütun Dönüşüm İşlemleri
from sklearn.preprocessing import OneHotEncoder, StandardScaler # kategori - sayısaş dönüşüm ve ölçeklendirme
from sklearn.pipeline import Pipeline # veri işleme hattı

In [17]:
!pip install xlrd

In [19]:
df = pd.read_excel('cars.xls')
df

Price  Mileage    Make     Model           Trim   Type  Cylinder  \
0    17314.103129     8221   Buick   Century       Sedan 4D  Sedan         6   
1    17542.036083     9135   Buick   Century       Sedan 4D  Sedan         6   
2    16218.847862    13196   Buick   Century       Sedan 4D  Sedan         6   
3    16336.913140    16342   Buick   Century       Sedan 4D  Sedan         6   
4    16339.170324    19832   Buick   Century       Sedan 4D  Sedan         6   
..            ...      ...     ...       ...            ...    ...       ...   
799  16507.070267    16229  Saturn  L Series  L300 Sedan 4D  Sedan         6   
800  16175.957604    19095  Saturn  L Series  L300 Sedan 4D  Sedan         6   
801  15731.132897    20484  Saturn  L Series  L300 Sedan 4D  Sedan         6   
802  15118.893228    25979  Saturn  L Series  L300 Sedan 4D  Sedan         6   
803  13585.636802    35662  Saturn  L Series  L300 Sedan 4D  Sedan         6   

     Liter  Doors  Cruise  Sound  Leather  
0      3.1      4       1      1        1  
1      3.1      4       1      1        0  
2      3.1      4       1      1        0  
3      3.1      4       1      0        0  
4      3.1      4       1      0        1  
..     ...    ...     ...    ...      ...  
799    3.0      4       1      0        0  
800    3.0      4       1      1        0  
801    3.0      4       1      1        0  
802    3.0      4       1      1        0  
803    3.0      4       1      0        0  

[804 rows x 12 columns]

In [21]:
# Data preprocessing

In [23]:
X = df.drop('Price', axis=1) # fiyata etki edenleri al
y = df['Price'] # tahmin

In [25]:
X_train, X_test , y_train, y_test = train_test_split(X,y, test_size = 0.2 , random_state = 42)

# data preprocessing, standardization and with  one hot encoding process automating

In [30]:
preprocess = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(),['Mileage','Cylinder','Liter','Doors']),
        ('cat', OneHotEncoder(),['Make','Model','Trim','Type'])
    ]
)
    

In [34]:
#modeli tnaımladık
my_model = LinearRegression()

In [36]:
pipe = Pipeline(steps=[('preprocessor',preprocess),('model',my_model)])

In [38]:
pipe.fit(X_train,y_train)

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(transformers=[('num', StandardScaler(),
                                                  ['Mileage', 'Cylinder',
                                                   'Liter', 'Doors']),
                                                 ('cat', OneHotEncoder(),
                                                  ['Make', 'Model', 'Trim',
                                                   'Type'])])),
                ('model', LinearRegression())])

In [40]:
y_pred = pipe.predict(X_test)
print('MSE',mean_squared_error(y_test,y_pred)**0.5)
print('R2', r2_score(y_test,y_pred))


MSE 835.100716728648
R2 0.9912072828879327


In [50]:
#istersek veri setinin tamamıyla tekrar eğitim yapabiliriz.
#pipe.fit(X,y)

# streamlit ile modeli Deploy etme / Yayma / Kullanıma Sunma/ Mlops

In [45]:
!pip install streamlit

  Obtaining dependency information for streamlit from https://files.pythonhosted.org/packages/0e/86/69fdac2ec6852304bda08e5af5b72dfa6e74dc0b3cef0d7c1e19994388ae/streamlit-1.35.0-py2.py3-none-any.whl.metadata
  Obtaining dependency information for blinker<2,>=1.0.0 from https://files.pythonhosted.org/packages/bb/2a/10164ed1f31196a2f7f3799368a821765c62851ead0e630ab52b8e14b4d0/blinker-1.8.2-py3-none-any.whl.metadata
  Using cached blinker-1.8.2-py3-none-any.whl.metadata (1.6 kB)
  Obtaining dependency information for cachetools<6,>=4.0 from https://files.pythonhosted.org/packages/fb/2b/a64c2d25a37aeb921fddb929111413049fc5f8b9a4c1aefaffaafe768d54/cachetools-5.3.3-py3-none-any.whl.metadata
  Obtaining dependency information for rich<14,>=10.14.0 from https://files.pythonhosted.org/packages/87/67/a37f6214d0e9fe57f6ae54b2956d550ca8365857f42a1ce0392bb21d9410/rich-13.7.1-py3-none-any.whl.metadata
  Obtaining dependency information for tenacity<9,>=8.1.0 from https://files.pythonhosted.org/packa

# python ile yapılan çalışmaların hızlı bir şekilde deployment süreçleri - HTML Rendering

In [56]:
import streamlit as st
#price tahmin fonksiyonu tanımla
def price(make,model,trim,mileage,car_type,cylinder,liter,doors,cruise,sound,leather):
    input_data=pd.DataFrame({'Make':[make],
                             'Model':[model],
                             'Trim':[trim],
                             'Mileage':[mileage],
                             'Type':[car_type],
                             'Cylinder':[cylinder],
                             'Liter':[liter],
                             'Doors':[doors],
                             'Cruise':[cruise],
                             'Sound':[sound],
                             'Leather':[leather]})
    prediction = pipe.predict(input_data)[0]
    return prediction


st.title("Car Price Prediction: red_car: @ErayCoşkunAI")
st.write('Select feature of the car')
make = st.selectbox("Brand of Car",df['Make'].unique())
model = st.selectbox("Model of Car",df[df['Make']==make]['Model'].unique())
trim = st.selectbox('Trim Of Car', df[(df['Make']==make) & (df['Model']==model)]['Trim'].unique())
mileage = st.number_input('Kilometer of Car',100,200000)
car_type = st.selectbox('Type Of Car', df['Type'].unique())
cylinder = st.selectbox('Cylinder of Car',df['Cylinder'].unique())
liter = st.number_input('Liter value of car',1,10)
doors = st.selectbox('Count of Door',df['Doors'].unique())
cruise = st.radio('Hız sbt', [True,False])
sound = st.radio('Sound System',[True,False])
leather = st.radio('Deri Döşeme',[True,False])
if st.button('Tahmin'):
    pred = price(make,model,trim,mileage,car_type,cylinder,liter,doors,cruise,sound,leather)
    st.write('Price:$',round(pred[0],2))


2024-06-11 20:10:16.914 Session state does not function when running a script without `streamlit run`
